In [149]:
from embedding import E5LargeEmbeddingFunction
from collections import defaultdict

import clickhouse_connect
import pandas as pd
import logging

client = clickhouse_connect.get_client(host='y1jzidyt9q.us-east-2.aws.clickhouse.cloud', port=8443, username='default', password='_lQ_JWXYQD3ym')
emb_func = E5LargeEmbeddingFunction()

In [123]:
def get_window_range(num, window_range):
    answer = [num]
    while len(answer) < window_range:
        f = 0
        left = answer[0] - 1
        right = answer[-1] + 1

        if left >= 0:
            answer = [left] + answer
            if len(answer) >= window_range:
                return answer

        answer.append(right)
    
    return answer

In [124]:
def _clickhouse_query_l2(query, client, emb_func, limit=5):
    emb_func.change_mode('query')
    embeddings = emb_func(query)[0]

    result = client.query(f'''SELECT
        ID, chunk_id,
        L2Distance(embedding, {embeddings}) AS score
    FROM index_texts
    ORDER BY score ASC
    LIMIT {limit}''')

    return result.result_rows

In [125]:
def _clickhouse_query_window(query, client, emb_func, limit=5, window=5):
    res = _clickhouse_query_l2(query, client, emb_func, limit=limit)

    window_sql_query = ''
    for i, row in enumerate(res):
        #ids_with_chunks[row[0]].extend(get_window_range(row[1], window))
        if i > 0:
            window_sql_query += ' UNION DISTINCT '
        window_sql_query += f'''SELECT * FROM index_texts WHERE ID = {row[0]} and chunk_id in {tuple(get_window_range(row[1], window))}'''

    result = client.query(window_sql_query)
    return result.result_rows

In [126]:
for row in _clickhouse_query_window('оформить кредит на мою маму', client, emb_func, limit=100, window=3):
    print(row)
    print(row[3])

(174, 22, 'https://cbr.ru//Queries/UniDbQuery/File/90134/2858', " ПoЛьзoBaTeЛIo плaтфopмы ДoсTyПa к ПJIaTфopмe цифpoвoгo pyбля BзaиМoДействиe ПoЛЬзoBaTeЛя плaTфopмьl с Бaнкoм Poссии oбеспечивaeтся с исПoЛЬзoBaниеМ изBещeний, yведoмлений, paсПopлкeниЙ, IIaПpaBЛяеМЬIх ПoЛЬзoBaTеЛеМ плaтфopмьl с ПpиМeнeниеМ пpилo) кения 15 кЛиeIITa ' ПpеДoсTaBЛeIIHoГo yчaсTI { икoM ПJIaTфopМьI ' B BиДе эЛeкTpoнньIХ сooбщений. 4.6.. (oстyп к плaтфopмe цифpoвoгo pyбля yЧaсTllикa плaтфopМЬI, ПoЛЬзoBaTеЛя плaтфopмьI пpиoсTaнaBлиBaeтся Бaнкoм Poссии ПyTeМ ПpeкpaщeЕИЯ BзaиМoДеЙcтвия с rlaсTникoМ плaтфopмьr, ПoЛЬзoBaTеJIеМ плaтфopмьr с исПoJIЬзoBaниеM эЛrкTpoIIнЬIx сooбщeний B сЛyЧaе BoзIIикHoBeHия Чp eзBьIЧaйньIx cиту aциiт ' o Пep aциo ннЬIx сбoев., (oстyп к плaтфopме цифpoвoгo pyбля rlaсTникa ппaтфopмьI, ПoЛьзOBaTeJIя IIЛaTфopмьl вoзoбнoвЛяеTся Бaнкoм Poссии пoсЛе yсTpaнения ПoсЛrДсTвий upeзвьIчaйньrx сиTyaций, oпеpaциoннЬIx сбoев. Бaнк Poссии незaМeДЛиTeЛЬнo инфopмиpyeT yчaсTникoв плaтфopMЬI ' ПoЛЬзoBaTелeй 

In [135]:
data.iloc[174]

link           https://cbr.ru//Queries/UniDbQuery/File/90134/...
text           цЕ}ITPAЛЬнЬrЙ БAHк PoссиЙскoй ФBДЕPAции GAIrк ...
pages                                                        NaN
is_markdown                                                False
Name: 174, dtype: object

In [128]:
data = pd.read_csv('Corpus_v4.csv')
data.shape

(32103, 4)

In [129]:
data.dropna(subset=['text'], inplace=True)
data.drop_duplicates(subset='text', inplace=True)
data = data[data['text'].str.strip() != '']
data.reset_index(drop=True, inplace=True)
data.shape

(29242, 4)

In [69]:
res = _clickhouse_query_l2('купить уникальные золотые монеты', client, emb_func)

In [167]:
res = client.query(f'''
    SELECT *
    FROM 
        index_texts
    WHERE
        chunk_id = 0
    order by ID asc
    limit 3000
    offset 3000''')

res = res.result_rows

with open('rows.txt', 'w') as f:
    for row in res:
        f.write(f'index: {row[0]}, {row[3]} \n')

In [ ]:
errors = [174, 202, 203, 204, 1048 - 1053, 1162-1166, 1570 - 1572, 1602, 1604, 3010, 3017, 3024, 3033, 3312, 3390, 3397, 3409,
          3411, 3516, 3643, 3650, 3670, 3674, 3783, 3835, 3851, 3857, 
          3867, 3870, 3877, 3880, 3882, 33884, 3887, 3890, 3937, 3942, 3944, 3947, 3950, 3955, 
          3981, 3983, 3989, 4001, 4004, 4011, 4015, 4019, 4024, 4030, 4042, 4045, 4052, 4056, 4059, 4062, 4107, 4116, 4132,
          4154, 4229, 4316

In [168]:
data.iloc[3033]

link           https://cbr.ru//Content/Document/File/123728/c...
text                                                         86 
pages                                                       88.0
is_markdown                                                False
Name: 3033, dtype: object

In [144]:
for row in res.result_rows:
    print(row[0], row[3])

KeyboardInterrupt: 

In [102]:
window=5

window_sql_query = ''
for i, row in enumerate(res):
    #ids_with_chunks[row[0]].extend(get_window_range(row[1], window))
    if i > 0:
        window_sql_query += ' UNION DISTINCT '
    window_sql_query += f'''SELECT * FROM index_texts WHERE ID = {row[0]} and chunk_id in {tuple(get_window_range(row[1], window))}'''

result = client.query(window_sql_query)
for row in result.result_rows:
    print(row)

(2281, 0, 'https://cbr.ru//Content/Document/File/145782/coins_cbr_2022_pr.pdf', ' СЕРИЯ «ИСТОРИЧЕСКИЕ СОБЫТИЯ» HISTORICAL EVENTS SERIES', 0, [0.04344139248132706, -0.013093809597194195, -0.02887667343020439, -0.04186256602406502, 0.03471691533923149, -0.029531968757510185, -0.02673668973147869, 0.10153445601463318, 0.09412192553281784, -0.021929247304797173, 0.025504300370812416, 0.02842095121741295, -0.03722936660051346, -0.01014799065887928, -0.015470435842871666, -0.02467544935643673, -0.03324734792113304, 0.04855277016758919, -0.0014074755599722266, 0.009713017381727695, 0.03557945415377617, -0.0164401326328516, -0.06035260111093521, -0.025361690670251846, -0.040080733597278595, -0.01564004085958004, -0.014126590453088284, -0.0271231010556221, -0.019423730671405792, -0.05740168318152428, -0.007917541079223156, 0.0005825345288030803, -0.03380168601870537, -0.037218693643808365, 0.003797924844548106, 0.031004922464489937, 0.026787137612700462, 0.04488537460565567, -0.0542599298059940

In [99]:
d = {}

KeyError: 0

In [77]:
ids_with_chunks

defaultdict(list,
            {1952: [0, 1, 2, 3, 4],
             2281: [0, 1, 2, 3, 4],
             2321: [0, 1, 2, 3, 4],
             2261: [0, 1, 2, 3, 4],
             2267: [0, 1, 2, 3, 4]})

In [96]:
window_sql_query = ''
for i, (k, v) in enumerate(ids_with_chunks.items()):
    if i > 0:
        window_sql_query += ' UNION ALL '
    window_sql_query += f'''SELECT * FROM index_texts WHERE ID = {k} and chunk_id in {tuple(v)}'''
    
window_sql_query

'SELECT * FROM index_texts WHERE ID = 1952 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2281 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2321 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2261 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2267 and chunk_id in (0, 1, 2, 3, 4)'

In [98]:
result = client.query(window_sql_query)
for row in result.result_rows:
    print(row)

(1952, 0, 'https://cbr.ru//hd_base/seldomc/', ' Базы данных Котировки редких валют Курсы валют к доллару США на заданную дату Динамика курса заданной валюты к доллару США', 0, [0.02669902704656124, -0.025725161656737328, -0.040822550654411316, -0.018318643793463707, 0.013429258950054646, -0.016236204653978348, -0.017121678218245506, 0.08162964880466461, 0.07342529296875, -0.031194956973195076, 0.046875257045030594, 0.019426213577389717, -0.03225695714354515, 0.0032085629645735025, -0.005864734295755625, 0.00622314028441906, -0.038016147911548615, 0.03280050307512283, -0.01603180542588234, 0.006390362977981567, 0.032759763300418854, -4.647437162930146e-05, -0.03209870681166649, -0.02839742600917816, -0.039633143693208694, -0.027064036577939987, -0.03786955773830414, -0.03547101467847824, 0.0029091208707541227, -0.04915853217244148, -0.01963597908616066, 0.017102131620049477, 0.002590649062767625, -0.05121168866753578, -0.03817499801516533, 0.030823180451989174, 0.008691269904375076, 0.0

In [94]:
result = client.query(f'''
SELECT * FROM index_texts WHERE ID = 1952 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2281 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2321 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2261 and chunk_id in (0, 1, 2, 3, 4) UNION ALL SELECT * FROM index_texts WHERE ID = 2267 and chunk_id in (0, 1, 2, 3, 4)''')

In [95]:
for row in result.result_rows:
    print(row)

(1952, 0, 'https://cbr.ru//hd_base/seldomc/', ' Базы данных Котировки редких валют Курсы валют к доллару США на заданную дату Динамика курса заданной валюты к доллару США', 0, [0.02669902704656124, -0.025725161656737328, -0.040822550654411316, -0.018318643793463707, 0.013429258950054646, -0.016236204653978348, -0.017121678218245506, 0.08162964880466461, 0.07342529296875, -0.031194956973195076, 0.046875257045030594, 0.019426213577389717, -0.03225695714354515, 0.0032085629645735025, -0.005864734295755625, 0.00622314028441906, -0.038016147911548615, 0.03280050307512283, -0.01603180542588234, 0.006390362977981567, 0.032759763300418854, -4.647437162930146e-05, -0.03209870681166649, -0.02839742600917816, -0.039633143693208694, -0.027064036577939987, -0.03786955773830414, -0.03547101467847824, 0.0029091208707541227, -0.04915853217244148, -0.01963597908616066, 0.017102131620049477, 0.002590649062767625, -0.05121168866753578, -0.03817499801516533, 0.030823180451989174, 0.008691269904375076, 0.0